# Setting

In [ ]:
# copy LST20Corpus มาไว้ใน Colab
!cp "/content/drive/My Drive/AIFORTHAI-LST20Corpus.tar.gz" .

In [ ]:
# Install
!pip install kaggle -qq
!pip install datasets -qq #สำหรับโหลดdataset
!pip install transformers -qq #สำหรับเทรนโมเดล
!pip install seqeval -qq #สำหรับevaluation
!pip install pythainlp

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!pip install python-crfsuite

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!kaggle competitions download -c ss3-hackathon-online-natural-language-processing

ss3-hackathon-online-natural-language-processing.zip: Skipping, found more recently modified local copy (use --force to force download)


In [ ]:
!unzip -o /content/ss3-hackathon-online-natural-language-processing.zip

Archive:  /content/ss3-hackathon-online-natural-language-processing.zip
  inflating: LST20 Brief Specification.pdf  
  inflating: ne_list.txt             
  inflating: ne_sample_submission.csv  
  inflating: ne_test.txt             


In [ ]:
# Extract LST20Corpus
!tar -xzf "/content/AIFORTHAI-LST20Corpus.tar.gz"

In [ ]:
# Import Python library
import pandas as pd
import glob
import plotly.express as px
from tqdm import tqdm
from pathlib import Path
from collections import Counter, defaultdict
from datasets import load_dataset, load_metric
from pythainlp.tokenize import sent_tokenize

In [ ]:
samplesubmit = pd.read_csv('/content/ne_sample_submission.csv')
samplesubmit.head(5)

Id Predicted
0   1     B_TTL
1   2     B_PER
2   3     I_PER
3   4       NaN
4   5       NaN

In [ ]:
ne_list = pd.read_csv('/content/ne_list.txt')
ne_list

Empty DataFrame
Columns: [['B_BRN',  'B_DES',  'B_DTM',  'B_LOC',  'B_MEA',  'B_NUM',  'B_ORG',  'B_PER',  'B_TRM',  'B_TTL',  'E_BRN',  'E_DES',  'E_DTM',  'E_LOC',  'E_MEA',  'E_NUM',  'E_ORG',  'E_PER',  'E_TRM',  'E_TTL',  'I_BRN',  'I_DES',  'I_DTM',  'I_LOC',  'I_MEA',  'I_NUM',  'I_ORG',  'I_PER',  'I_TRM',  'I_TTL',  'O']]
Index: []

[0 rows x 31 columns]

# Prepare model for predict named entity

In [ ]:
#Dowload dataset of LST20
datasets = load_dataset("lst20", data_dir="/content/LST20_Corpus") 
datasets

  0%|          | 0/3 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['id', 'fname', 'tokens', 'pos_tags', 'ner_tags', 'clause_tags'],
        num_rows: 63310
    })
    validation: Dataset({
        features: ['id', 'fname', 'tokens', 'pos_tags', 'ner_tags', 'clause_tags'],
        num_rows: 5620
    })
    test: Dataset({
        features: ['id', 'fname', 'tokens', 'pos_tags', 'ner_tags', 'clause_tags'],
        num_rows: 5250
    })
})

In [ ]:
#Convert dataset to DataFrame
train_df = pd.DataFrame(datasets['train'])
validation_df = pd.DataFrame(datasets['validation'])
test_df = pd.DataFrame(datasets['test'])

In [ ]:
train_df

id       fname                                             tokens  \
0       0  T00126.txt  [สุรยุทธ์, ยัน, ปฏิเสธ, ลงนาม, _, MOU, _, กับ,...   
1       1  T00126.txt          [1, _, กันยายน, _, 2550, _, 12:21, _, น.]   
2       2  T00126.txt  [นายก, ฯ, _, ย้ำ, ไม่, ลงนาม, ใน, _, MOU, _, ร...   
3       3  T00126.txt  [ยัน, ไทย, ไม่, ได้, ล้มเหลว, ถึง, ขั้น, นั้น,...   
4       4  T00126.txt  [พร้อม, หนุน, กกต., จัด, เลือกตั้ง, ให้, บริสุ...   
...    ..         ...                                                ...   
63305   6  T13136.txt  [นาย, ปณิธาน, _, กล่าว, ว่า, _, หาก, การ, ยื่น...   
63306   7  T13136.txt  [เมื่อ, ถาม, ว่า, _, ใน, ทาง, การเมือง, _, หาก...   
63307   8  T13136.txt  [นาย, ปณิธาน, _, กล่าว, ว่า, _, เรื่อง, กฎหมาย...   
63308   9  T13136.txt  [หาก, เป็น, การ, ขอ, ถวาย, ฎีกา, ตาม, โบราณ, ร...   
63309  10  T13136.txt  [อย่างไรก็ตาม, _, หน่วยงาน, ราชการ, ต้อง, ให้,...   

                                                pos_tags  \
0                  [0, 1, 1, 1, 2, 0, 2, 4, 0, 12, 1, 0]   
1                           [8, 2, 0, 2, 8, 2, 8, 2, 10]   
2      [0, 2, 2, 1, 12, 1, 4, 2, 0, 2, 4, 0, 3, 5, 6,...   
3      [1, 0, 12, 5, 1, 1, 0, 9, 1, 7, 1, 0, 9, 12, 1...   
4                               [3, 1, 0, 1, 1, 3, 1, 1]   
...                                                  ...   
63305  [0, 0, 2, 1, 3, 2, 3, 7, 1, 0, 12, 1, 3, 5, 1,...   
63306  [4, 1, 3, 2, 4, 0, 0, 2, 3, 0, 3, 1, 0, 6, 2, ...   
63307  [0, 0, 2, 1, 3, 2, 0, 0, 5, 3, 1, 2, 7, 1, 1, ...   
63308  [3, 1, 7, 1, 1, 0, 4, 0, 0, 2, 5, 1, 0, 3, 0, ...   
63309  [3, 2, 0, 0, 5, 5, 0, 3, 1, 2, 3, 0, 3, 6, 1, ...   

                                                ner_tags  \
0                   [8, 0, 0, 0, 0, 0, 0, 0, 7, 0, 0, 0]   
1                      [3, 13, 13, 13, 23, 0, 3, 13, 23]   
2      [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 7, 0, 0, 0, ...   
3      [0, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
4                               [0, 0, 7, 0, 0, 0, 0, 0]   
...                                                  ...   
63305  [10, 8, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
63306  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
63307  [10, 8, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
63308  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 7, ...   
63309  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                             clause_tags  
0                   [1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 3]  
1                            [1, 2, 2, 2, 2, 2, 2, 2, 3]  
2      [1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 3, 1, 2, 2, ...  
3      [1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, ...  
4                               [1, 2, 2, 2, 3, 1, 2, 3]  
...                                                  ...  
63305  [1, 2, 2, 2, 3, 0, 1, 2, 2, 2, 2, 2, 2, 2, 2, ...  
63306  [1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, ...  
63307  [1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, ...  
63308  [1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 3, 1, 2, ...  
63309  [1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, ...  

[63310 rows x 6 columns]

In [ ]:
_POS_TAGS = ["NN", "VV", "PU", "CC", "PS", "AX", "AV", "FX", "NU", "AJ", "CL", "PR", "NG", "PA", "XX", "IJ"]
_NER_TAGS = [ "O",
        "B_BRN",
        "B_DES",
        "B_DTM",
        "B_LOC",
        "B_MEA",
        "B_NUM",
        "B_ORG",
        "B_PER",
        "B_TRM",
        "B_TTL",
        "I_BRN",
        "I_DES",
        "I_DTM",
        "I_LOC",
        "I_MEA",
        "I_NUM",
        "I_ORG",
        "I_PER",
        "I_TRM",
        "I_TTL",
        "E_BRN",
        "E_DES",
        "E_DTM",
        "E_LOC",
        "E_MEA",
        "E_NUM",
        "E_ORG",
        "E_PER",
        "E_TRM",
        "E_TTL",]
_CLAUSE_TAGS = ["O", "B_CLS", "I_CLS", "E_CLS"]

In [ ]:
def convert_to_simple_transformer_format(df):
  data_df = pd.DataFrame()
  sentence_id = []
  words = []
  labels = []

  for sentence in range(len(df)):
    for token in range(len(df['tokens'][sentence])):
      sentence_id.append(sentence)
      words.append(df['tokens'][sentence][token])
      labels.append(_NER_TAGS[df['ner_tags'][sentence][token]])

  return pd.DataFrame(
      {"sentence_id": sentence_id, "words": words, "labels": labels}
  )

In [ ]:
train_data = convert_to_simple_transformer_format(train_df)
validation_data = convert_to_simple_transformer_format(validation_df)
test_data = convert_to_simple_transformer_format(test_df)

In [ ]:
train_data

sentence_id     words labels
0                  0  สุรยุทธ์  B_PER
1                  0       ยัน      O
2                  0    ปฏิเสธ      O
3                  0     ลงนาม      O
4                  0         _      O
...              ...       ...    ...
2714721        63309       การ      O
2714722        63309       ถอน      O
2714723        63309   รายชื่อ      O
2714724        63309      ด้วย      O
2714725        63309         .      O

[2714726 rows x 3 columns]

# Model

In [ ]:
!pip install simpletransformers
!pip install python-crfsuite

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import torch
import pandas as pd
from simpletransformers.ner import NERModel, NERArgs

# Configure the model
ner_args = NERArgs()
ner_args.train_batch_size = 16
ner_args.eval_batch_size_batch_size = 16
ner_args.use_multiprocessing = True
ner_args.evaluate_during_training = True
ner_args.overwrite_output_dir = True
ner_args.num_train_epochs = 1
ner_args.max_seq_length = 128

model = NERModel(
    "camembert", "airesearch/wangchanberta-base-att-spm-uncased", args=ner_args, use_cuda=torch.cuda.is_available(), labels=_NER_TAGS
)

Some weights of the model checkpoint at airesearch/wangchanberta-base-att-spm-uncased were not used when initializing CamembertForTokenClassification: ['lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.decoder.bias', 'lm_head.dense.weight', 'lm_head.decoder.weight', 'lm_head.layer_norm.weight', 'lm_head.dense.bias']
- This IS expected if you are initializing CamembertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing CamembertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of CamembertForTokenClassification were not initialized from the model checkpoint at airesearch/wangchanberta-base-att-spm-uncased and are newly initialized: ['classifier

In [ ]:
# Train the model
model.train_model(train_data, eval_data = validation_data)

  0%|          | 0/63310 [00:00<?, ?it/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/3957 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/torch/optim/lr_scheduler.py:136: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  "https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate", UserWarning)


  0%|          | 0/2 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/703 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/seqeval/metrics/sequence_labeling.py:171: UserWarning: B_LOC seems not to be NE tag.
  warnings.warn('{} seems not to be NE tag.'.format(chunk))
/usr/local/lib/python3.7/dist-packages/seqeval/metrics/sequence_labeling.py:171: UserWarning: B_PER seems not to be NE tag.
  warnings.warn('{} seems not to be NE tag.'.format(chunk))
/usr/local/lib/python3.7/dist-packages/seqeval/metrics/sequence_labeling.py:171: UserWarning: B_NUM seems not to be NE tag.
  warnings.warn('{} seems not to be NE tag.'.format(chunk))
/usr/local/lib/python3.7/dist-packages/seqeval/metrics/sequence_labeling.py:171: UserWarning: B_DTM seems not to be NE tag.
  warnings.warn('{} seems not to be NE tag.'.format(chunk))
/usr/local/lib/python3.7/dist-packages/seqeval/metrics/sequence_labeling.py:171: UserWarning: I_DTM seems not to be NE tag.
  warnings.warn('{} seems not to be NE tag.'.format(chunk))
/usr/local/lib/python3.7/dist-packages/seqeval/metrics/sequence_labeling.py:171:

  0%|          | 0/2 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/703 [00:00<?, ?it/s]

(3957,
 defaultdict(list,
             {'global_step': [2000, 3957],
              'train_loss': [0.08452371507883072, 0.049386609345674515],
              'eval_loss': [0.14863835800449718, 0.13140853514376852],
              'precision': [0.7259496686446918, 0.7595179647400134],
              'recall': [0.7882607468723545, 0.8003480387545856],
              'f1_score': [0.7558231301720444, 0.7793986305448051]}))

In [ ]:
# Evaluate the model
result, model_outputs, preds_list = model.eval_model(validation_data)

  0%|          | 0/2 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/703 [00:00<?, ?it/s]

# Prepare test data by manage ne_test.txt file

In [ ]:
#Check word inside list
def data_inside(data_list):
  x = 0
  for i in range(len(data_list)):
    a = len(data_list[i])
    x = x+a 
  return x

In [ ]:
def blank_space(x):
  if x == '':
    x = '_'
  return x

In [ ]:
texts_test_raw = []
f = open("/content/ne_test.txt", 'r')
file_data = f.readlines()
for line in file_data:
  line = line.strip().replace(u'\xa0', u' ')
  texts_test_raw.append(line)

In [ ]:
len(texts_test_raw)

69562

In [ ]:
texts_test_raw = texts_test_raw[:-1]

In [ ]:
print(texts_test_raw)

['นาง', 'สุดารัตน์', '', 'เกยุราพันธ์', '', 'รมว.', 'สาธารณสุข', '', 'แถลง', 'ถึง', 'การ', 'จัด', 'งาน', 'มหกรรม', 'กิน', 'ไก่', 'ไทย', 'ปลอด', 'ภัย', '', '100', '%', '', 'ว่า', '', 'รัฐบาล', 'ร่วม', 'กับ', 'กทม.', 'จัด', 'งาน', 'ดัง', 'กล่าว', 'ขึ้น', 'ที่', 'ท้องสนามหลวง', 'ใน', 'วัน', 'เสาร์', 'ที่', '', '7', '', 'ก.พ.', 'นี้', '', 'ตั้งแต่', '', '16.00', 'น.', 'เป็นต้นไป', '', 'ส่วน', 'พ.ต.ท.', 'ทักษิณ', '', 'ชินวัตร', 'รัฐมนตรี', '', 'จะ', 'เดินทาง', 'มา', 'ถึง', 'ที่', 'งาน', 'ใน', 'เวลา', '', '16.30', 'น.', '', 'เพื่อ', 'เยี่ยมชม', 'นิทรรศการ', '', 'และ', 'ประกอบ', 'อาหาร', 'เมนู', '', 'กระเพรา', 'ไก่', 'ไข่ดาว', 'สุก', '', 'ไก่', 'ทอด', '', 'ด้วย', 'ตัว', 'เอง', 'และ', 'แจกจ่าย', 'ให้', 'กับ', 'ประชาชน', '', 'โดย', 'จะ', 'มี', 'นาย', 'สมัคร', '', 'สุนทรเวช', '', 'ผู้', 'ว่า', 'ฯ', 'กทม.', '', 'และ', 'ม.ล.', 'ศิริเฉลิม', '', 'สวัสดิวัฒน์', '', 'หรือ', 'หมึกแดง', '', 'ร่วม', 'ปรุง', 'อาหาร', 'ด้วย', '', 'ภาย', 'หลัง', 'ที่', 'นายก', 'ฯ', 'ปรุง', 'อาหาร', 'เสร็จ', 'จะ', 'ร่วม', 'ร

In [ ]:
for i in range (len(texts_test_raw)):
  texts_test_raw[i] = blank_space(texts_test_raw[i])

In [ ]:
print(len(texts_test_raw))
print(texts_test_raw)

69561
['นาง', 'สุดารัตน์', '_', 'เกยุราพันธ์', '_', 'รมว.', 'สาธารณสุข', '_', 'แถลง', 'ถึง', 'การ', 'จัด', 'งาน', 'มหกรรม', 'กิน', 'ไก่', 'ไทย', 'ปลอด', 'ภัย', '_', '100', '%', '_', 'ว่า', '_', 'รัฐบาล', 'ร่วม', 'กับ', 'กทม.', 'จัด', 'งาน', 'ดัง', 'กล่าว', 'ขึ้น', 'ที่', 'ท้องสนามหลวง', 'ใน', 'วัน', 'เสาร์', 'ที่', '_', '7', '_', 'ก.พ.', 'นี้', '_', 'ตั้งแต่', '_', '16.00', 'น.', 'เป็นต้นไป', '_', 'ส่วน', 'พ.ต.ท.', 'ทักษิณ', '_', 'ชินวัตร', 'รัฐมนตรี', '_', 'จะ', 'เดินทาง', 'มา', 'ถึง', 'ที่', 'งาน', 'ใน', 'เวลา', '_', '16.30', 'น.', '_', 'เพื่อ', 'เยี่ยมชม', 'นิทรรศการ', '_', 'และ', 'ประกอบ', 'อาหาร', 'เมนู', '_', 'กระเพรา', 'ไก่', 'ไข่ดาว', 'สุก', '_', 'ไก่', 'ทอด', '_', 'ด้วย', 'ตัว', 'เอง', 'และ', 'แจกจ่าย', 'ให้', 'กับ', 'ประชาชน', '_', 'โดย', 'จะ', 'มี', 'นาย', 'สมัคร', '_', 'สุนทรเวช', '_', 'ผู้', 'ว่า', 'ฯ', 'กทม.', '_', 'และ', 'ม.ล.', 'ศิริเฉลิม', '_', 'สวัสดิวัฒน์', '_', 'หรือ', 'หมึกแดง', '_', 'ร่วม', 'ปรุง', 'อาหาร', 'ด้วย', '_', 'ภาย', 'หลัง', 'ที่', 'นายก', 'ฯ', 'ปรุง', '

In [ ]:
from pythainlp.tokenize import clause_tokenize

# Sentence Cut by LST20 dataset
my_token = clause_tokenize(texts_test_raw)


/usr/local/lib/python3.7/dist-packages/pythainlp/tokenize/crfcls.py:63: UserWarning: 
    LST20 corpus are free for research and open source only.

    If you want to use in Commercial use, please contract NECTEC.

    https://www.facebook.com/dancearmy/posts/10157641945708284
    
  """)
/usr/local/lib/python3.7/dist-packages/pythainlp/tag/perceptron.py:47: UserWarning: 
    LST20 corpus are free for research and open source only.

    If you want to use in Commercial use, please contract NECTEC.

    https://www.facebook.com/dancearmy/posts/10157641945708284
    
  """


In [ ]:
print(len(my_token)) #จำนวนประโยค

3648


In [ ]:
print(my_token) #แต่ละคำที่อยู่ในประโยค

[['นาง', 'สุดารัตน์', '_', 'เกยุราพันธ์', '_', 'รมว.', 'สาธารณสุข', '_', 'แถลง', 'ถึง', 'การ', 'จัด', 'งาน', 'มหกรรม', 'กิน', 'ไก่', 'ไทย', 'ปลอด', 'ภัย', '_', '100', '%', '_', 'ว่า', '_', 'รัฐบาล', 'ร่วม', 'กับ', 'กทม.', 'จัด', 'งาน', 'ดัง', 'กล่าว', 'ขึ้น', 'ที่', 'ท้องสนามหลวง', 'ใน', 'วัน', 'เสาร์', 'ที่', '_', '7', '_', 'ก.พ.', 'นี้', '_', 'ตั้งแต่', '_', '16.00', 'น.', 'เป็นต้นไป', '_', 'ส่วน', 'พ.ต.ท.', 'ทักษิณ', '_', 'ชินวัตร', 'รัฐมนตรี', '_', 'จะ', 'เดินทาง', 'มา', 'ถึง', 'ที่', 'งาน', 'ใน', 'เวลา', '_', '16.30', 'น.', '_', 'เพื่อ', 'เยี่ยมชม', 'นิทรรศการ', '_', 'และ', 'ประกอบ', 'อาหาร', 'เมนู', '_', 'กระเพรา', 'ไก่', 'ไข่ดาว', 'สุก', '_', 'ไก่', 'ทอด', '_', 'ด้วย', 'ตัว', 'เอง'], ['และ', 'แจกจ่าย', 'ให้', 'กับ', 'ประชาชน', '_', 'โดย', 'จะ', 'มี', 'นาย', 'สมัคร', '_', 'สุนทรเวช', '_', 'ผู้', 'ว่า', 'ฯ', 'กทม.', '_', 'และ', 'ม.ล.', 'ศิริเฉลิม', '_', 'สวัสดิวัฒน์', '_', 'หรือ', 'หมึกแดง', '_', 'ร่วม', 'ปรุง', 'อาหาร', 'ด้วย', '_', 'ภาย'], ['หลัง', 'ที่', 'นายก', 'ฯ', 'ปรุง', 'อ

In [ ]:
print(my_token[0])

['นาง', 'สุดารัตน์', '_', 'เกยุราพันธ์', '_', 'รมว.', 'สาธารณสุข', '_', 'แถลง', 'ถึง', 'การ', 'จัด', 'งาน', 'มหกรรม', 'กิน', 'ไก่', 'ไทย', 'ปลอด', 'ภัย', '_', '100', '%', '_', 'ว่า', '_', 'รัฐบาล', 'ร่วม', 'กับ', 'กทม.', 'จัด', 'งาน', 'ดัง', 'กล่าว', 'ขึ้น', 'ที่', 'ท้องสนามหลวง', 'ใน', 'วัน', 'เสาร์', 'ที่', '_', '7', '_', 'ก.พ.', 'นี้', '_', 'ตั้งแต่', '_', '16.00', 'น.', 'เป็นต้นไป', '_', 'ส่วน', 'พ.ต.ท.', 'ทักษิณ', '_', 'ชินวัตร', 'รัฐมนตรี', '_', 'จะ', 'เดินทาง', 'มา', 'ถึง', 'ที่', 'งาน', 'ใน', 'เวลา', '_', '16.30', 'น.', '_', 'เพื่อ', 'เยี่ยมชม', 'นิทรรศการ', '_', 'และ', 'ประกอบ', 'อาหาร', 'เมนู', '_', 'กระเพรา', 'ไก่', 'ไข่ดาว', 'สุก', '_', 'ไก่', 'ทอด', '_', 'ด้วย', 'ตัว', 'เอง']


In [ ]:
data_inside(my_token)

69561

# Make predictions

In [ ]:
#Test model
# Configure the model
ner_args = NERArgs()
ner_args.train_batch_size = 16
ner_args.eval_batch_size_batch_size = 16
ner_args.use_multiprocessing = True
ner_args.evaluate_during_training = True
ner_args.overwrite_output_dir = True
ner_args.num_train_epochs = 3
ner_args.max_seq_length = 512

best_model = NERModel(
    "camembert", "/content/outputs/best_model", args=ner_args, use_cuda=torch.cuda.is_available(), labels=_NER_TAGS
)

In [ ]:
# Make predictions with the model
predictions, raw_outputs = best_model.predict(my_token, False)

  0%|          | 0/3648 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/456 [00:00<?, ?it/s]

In [ ]:
predictions

[[{'นาง': 'B_TTL'},
  {'สุดารัตน์': 'B_PER'},
  {'_': 'I_PER'},
  {'เกยุราพันธ์': 'E_PER'},
  {'_': 'O'},
  {'รมว.': 'B_DES'},
  {'สาธารณสุข': 'B_ORG'},
  {'_': 'O'},
  {'แถลง': 'O'},
  {'ถึง': 'O'},
  {'การ': 'O'},
  {'จัด': 'O'},
  {'งาน': 'O'},
  {'มหกรรม': 'O'},
  {'กิน': 'O'},
  {'ไก่': 'O'},
  {'ไทย': 'B_LOC'},
  {'ปลอด': 'O'},
  {'ภัย': 'O'},
  {'_': 'O'},
  {'100': 'B_MEA'},
  {'%': 'E_MEA'},
  {'_': 'O'},
  {'ว่า': 'O'},
  {'_': 'O'},
  {'รัฐบาล': 'O'},
  {'ร่วม': 'O'},
  {'กับ': 'O'},
  {'กทม.': 'B_ORG'},
  {'จัด': 'O'},
  {'งาน': 'O'},
  {'ดัง': 'O'},
  {'กล่าว': 'O'},
  {'ขึ้น': 'O'},
  {'ที่': 'O'},
  {'ท้องสนามหลวง': 'B_LOC'},
  {'ใน': 'O'},
  {'วัน': 'B_DTM'},
  {'เสาร์': 'I_DTM'},
  {'ที่': 'I_DTM'},
  {'_': 'I_DTM'},
  {'7': 'I_DTM'},
  {'_': 'I_DTM'},
  {'ก.พ.': 'E_DTM'},
  {'นี้': 'O'},
  {'_': 'O'},
  {'ตั้งแต่': 'O'},
  {'_': 'O'},
  {'16.00': 'B_DTM'},
  {'น.': 'E_DTM'},
  {'เป็นต้นไป': 'O'},
  {'_': 'O'},
  {'ส่วน': 'O'},
  {'พ.ต.ท.': 'B_DES'},
  {'ทักษิณ': 'B_PE

In [ ]:
len(predictions)

3648

In [ ]:
data_inside(predictions)

69561

In [ ]:
final_test = []

for i in range (len(predictions)):
  for j in range (len(predictions[i])):
    data = predictions[i][j]
    value = data.values()
    final_test += value

len(final_test)

69561

# Submission

In [ ]:
samplesubmit

Id Predicted
0          1     B_TTL
1          2     B_PER
2          3     I_PER
3          4       NaN
4          5       NaN
...      ...       ...
69556  69557       NaN
69557  69558       NaN
69558  69559       NaN
69559  69560       NaN
69560  69561       NaN

[69561 rows x 2 columns]

In [ ]:
predicts = samplesubmit
predicts['Predicted'] = final_test
predicts

Id Predicted
0          1     B_TTL
1          2     B_PER
2          3     I_PER
3          4     E_PER
4          5         O
...      ...       ...
69556  69557         O
69557  69558         O
69558  69559         O
69559  69560         O
69560  69561         O

[69561 rows x 2 columns]

In [ ]:
predicts.to_csv('submission_nlp_02.csv',index=False)